In [49]:
import numpy as np
import random

import pandas as pd
import sklearn as sk
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold,RepeatedStratifiedKFold, cross_val_score, cross_validate
from sklearn import svm
from sklearn import metrics
from sklearn.metrics import  accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB, MultinomialNB, CategoricalNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn import tree
from sklearn.svm import LinearSVC
from sklearn.feature_selection import SelectFromModel
import os
import matplotlib.pyplot as plt
import shutil
import seaborn as sns
from matplotlib.ticker import StrMethodFormatter
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler,MinMaxScaler
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.svm import SVC
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.feature_selection import RFECV
from sklearn.datasets import make_classification
from sklearn.svm import SVC
from sklearn.datasets import load_digits
from sklearn.feature_selection import RFE
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt  
from sklearn.datasets import load_digits
from sklearn.feature_selection import SelectKBest, chi2,f_classif
from sklearn import preprocessing
import math
from sklearn.metrics import fbeta_score
from numpy import arange
from sklearn.metrics import balanced_accuracy_score

In [50]:
metric_to_optimize = 'MCC'

In [51]:
from warnings import simplefilter
# ignore all future warnings
simplefilter(action='ignore', category=FutureWarning)
simplefilter(action='ignore', category=RuntimeWarning)

In [52]:
def print_and_summarize_best_model(results,ml_results,best_models):
    ml_results = pd.concat([ml_results, results],sort=True)
    best_model_index = np.argmax(np.array(results[metric_to_optimize]))
    best_model = results.iloc[best_model_index]
    best_models = pd.concat([best_models, pd.DataFrame(best_model).transpose()],sort = True)
    
    return ml_results,best_models,best_model_index

In [53]:
def init_metrics():
    '''
    initialize the (empty) metrics structures
    :return: metrics_results
    '''
    metrics_results = {'FNR': None, 'FPR': None, 'MCC':None, 'ACC': None, 'F1score': None,'F2score': None}
    metrics_results['FNR'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    metrics_results['FPR'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    metrics_results['MCC'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    metrics_results['ACC'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    metrics_results['F1score'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    metrics_results['F2score'] = {'DT':None,'SVM':None,'RF':None,'NB': None,'KNN':None,'LogisticRegression':None}
    return metrics_results

def init_best_models():
    best_models = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    return best_models

def init_ml_results():
    ml_results = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    return ml_results

In [54]:
def calculate_metrics(classifier_name,y_test,y_prediction,metrics_results,Type_test):
    '''
    calculate each metric for evaluation
    :param classifier_name: name of classifier used (svm, NB, etc)
    :param y_test:
    :param y_prediction:
    :param metrics_results:
    :return:
    '''
    from sklearn.metrics import matthews_corrcoef
    FNR_Leak = len(y_prediction[(Type_test =='Leak')& (y_prediction==0)])*1.00/len(Type_test[(Type_test =='Leak')])
    FNR_Clog = len(y_prediction[(Type_test =='Clog')& (y_prediction==0)])*1.00/len(Type_test[(Type_test =='Clog')])

    TN, FP, FN, TP = confusion_matrix(y_test, y_prediction).ravel()
      
    TPR = TP / (TP + FN)
    FPR  = FP / (FP + TN)
    TNR = TN / (TN + FP)
    FNR = FN / (FN + TP)
    F1_Score = fbeta_score(y_test, y_prediction, beta=1)
    F2_Score = fbeta_score(y_test, y_prediction, beta=2)
#     AUC = roc_auc_score(y_test, y_prediction,average='weighted')#average='weighted': Calculate metrics for each label, and find their average, weighted by support (the number of true instances for each label)
    MCC = matthews_corrcoef(y_test, y_prediction)
    Accuracy = accuracy_score(y_test, y_prediction)
    balanced_ACC = balanced_accuracy_score(y_test, y_prediction)

    metrics_results['FNR'][classifier_name] =  {'FNR':FNR,'Leak':FNR_Leak,'Clog':FNR_Clog,'balanced_ACC':balanced_ACC}
    metrics_results['FPR'][classifier_name] = FPR
    metrics_results['MCC'][classifier_name] = MCC
    metrics_results['ACC'][classifier_name] = Accuracy
    metrics_results['F1score'][classifier_name] = F1_Score
    metrics_results['F2score'][classifier_name] = F2_Score
    
    return metrics_results

In [32]:
def save_folds_for_best_model(model_index,folds,MCC_results,F1score_results,F2score_results,FNR_results):
    print(model_index)
    folder_path = 'C:\\Users\\noy\\Desktop\\תזה\\Results\\Kedma_and_Lavi_secend_best_model_'
    balanced_ACC_results = pd.DataFrame(d['balanced_ACC'] for d in FNR_results).values.ravel()
    Al = 'RF_115_binary'

    best_mudel_res= pd.DataFrame(data={'Algorithm':Al,
                                          'Fold_number':folds,
                                          'MCC': MCC_results,
                                           'balanced_ACC':balanced_ACC_results,
                                          'F1score': F1score_results,
                                          'F2score': F2score_results})
    best_mudel_res =best_mudel_res.set_index('Fold_number')
    best_mudel_res.to_csv(folder_path+Al+'_folds_results.csv')
    print('Created')
    return

In [55]:
def CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params):
#     if(model_index==115):
    folds,FNR_results, FPR_results, MCC_results, ACC_results,F1score_results,F2score_results = [],[],[],[],[],[],[]                      
    random.seed(10)
    skf = RepeatedStratifiedKFold(n_splits=5,n_repeats=5, random_state=12)
    Type = data_labels['Type']
    data_labels = data_labels.drop("Type",axis=1)
    fold=1
    # K_folds:
    for train_index, test_index in skf.split(data, data_labels):
        x_train_fold, x_test_fold = data.iloc[train_index], data.iloc[test_index]
        y_train_fold, y_test_fold = data_labels.iloc[train_index], data_labels.iloc[test_index]
        Type_test = Type.iloc[test_index]

        if (Algorithm not in ['RF','DT']):
            if (Algorithm in('NB','svm_linear')):
                scaler = MinMaxScaler()
            else:
                scaler = StandardScaler()
            x_train_fold = scaler.fit_transform(x_train_fold)
            x_test_fold = scaler.fit_transform(x_test_fold)

        classifier.fit(x_train_fold, y_train_fold.values.ravel())
        y_prediction = classifier.predict(x_test_fold)
        metrics_results = calculate_metrics(Algorithm,y_test_fold,y_prediction,metrics_results,Type_test)
        FNR_results.append(metrics_results['FNR'][Algorithm])
        FPR_results.append(metrics_results['FPR'][Algorithm])
        MCC_results.append(metrics_results['MCC'][Algorithm])
        ACC_results.append(metrics_results['ACC'][Algorithm])
        F1score_results.append(metrics_results['F1score'][Algorithm])
        F2score_results.append(metrics_results['F2score'][Algorithm])
        folds.append(fold)
        fold =fold+1

#         save_folds_for_best_model(model_index,folds,MCC_results,F1score_results,F2score_results,FNR_results)

    results_summary = results_summary.append({'Algorithm':Algorithm,
                                              'model_index':model_index,
                                              'parameters':params,
                                              'FNR': {'FNR':sum(d['FNR'] for d in FNR_results) / len(FNR_results),
                                                     'FNR_Leak':sum(d['Leak'] for d in FNR_results) / len(FNR_results),
                                                     'FNR_Clog':sum(d['Clog'] for d in FNR_results) / len(FNR_results),
                                                     'balanced_ACC':sum(d['balanced_ACC'] for d in FNR_results) / len(FNR_results)},#np.mean(FNR_results),
                                              'FPR': np.mean(FPR_results),
                                              'MCC': np.mean(MCC_results),
                                              'ACC': np.mean(ACC_results),
                                              'F1score': np.mean(F1score_results),
                                              'F2score': np.mean(F2score_results)},
                                             ignore_index=True)
    return results_summary

In [56]:
def train_test_CV_LogisticRegression(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])

    Algorithm = 'LogisticRegression'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    cs = [0.1, 1, 10, 100]
    solvers = ['lbfgs', 'liblinear', 'sag', 'saga']
    penalties_lbfgs_sag = ['l2', 'none']                # Used to specify the norm used in the penalization.
    penalties_liblinear = ['l1', 'l2']
    penalties_saga = ['l2', 'elasticnet', 'none']
    class_weight = 'balanced'
    multi_class = 'ovr'
    l1_ratio = []

    for s in solvers:
        if(s=='lbfgs' or s=='sag'):
            penalties = penalties_lbfgs_sag
        if(s=='liblinear'):
            penalties = penalties_liblinear
        if (s == 'saga'):
            penalties = penalties_saga
        for p in penalties:
            if (p == 'elasticnet'):
                l1_ratio = arange(0.01, 0.99, 0.01)
            for c in cs:
                for l1_r in l1_ratio:
                    classifier = LogisticRegression(penalty=p,C=c,class_weight='balanced',
                                                    random_state=0,multi_class='ovr',
                                                    solver=s,l1_ratio=l1_r,
                                                    max_iter=10000)  # create classifier
                    params = {"penalty": p,"C": c,"solver":s,"l1_ratio":l1_r}
                    results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)
                    model_index+=1
#     results_summary['model_index'] = results_summary['model_index'].astype(int)
#     results_summary = results_summary.set_index('model_index')
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results

In [57]:
def train_test_CV_RandomForest(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'RF'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)

    
    n_estimators = [200, 500]               # number of trees in the foreset
    max_depth = [5, 8, 10, 20]              # max number of levels in each decision tree
    criterion = ['gini', 'entropy']
    min_samples_split = [2, 5, 10, 15,20]   # min number of data points placed in a node before the node is split, used to control over-fitting
    bootstrap = [True, False]
    for n in n_estimators:
        for max in max_depth:
            for c in criterion:
                for min_sample in min_samples_split:
                    for b in bootstrap:
                        classifier = RandomForestClassifier(random_state=12,class_weight='balanced', n_estimators=n,
                                                            max_depth=max, criterion=c,min_samples_split=min_sample,bootstrap=b)  # class_weight: misclassifying the rare class is punished harsher.
                                           
                        params = {"n_estimators": n,"criterion": c,"min_samples_split":min_sample,"bootstrap":b,'max_depth':max}
                        results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)

                        model_index+=1

    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results

In [58]:
def train_test_CV_svm_linear(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'svm_linear'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    kernel = 'linear'
    cs = [0.1, 1, 10, 100]
    for c in cs:
        classifier = svm.SVC(probability=True,kernel=kernel,C=c,max_iter=100000)
        params = {"kernel": kernel,"C": c}
        results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,
                                           metrics_results,results_summary,params)
        model_index+=1

    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [59]:
def train_test_CV_svm_rbf(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'svm_rbf'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    kernel =  'rbf'
    cs = [0.1, 1, 10, 100]
    gammas = [0.0001, 0.001, 0.01, 0.1, 1, 2, 3, 4]
    for c in cs:
        for gamma in gammas:
            classifier = svm.SVC(probability=True,kernel=kernel,C=c,gamma=gamma,max_iter=100000)
            params = {"kernel": kernel,"C": c,'gamma':gamma}
            results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)

            model_index+=1
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [60]:
def train_test_CV_svm_poly(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'svm_poly'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    kernel = 'poly'
    cs = [0.1, 1, 10, 100]
    gammas = [0.0001, 0.001, 0.01, 0.1, 1]
    degrees = [2,3,4,5]
    for c in cs:
        for gamma in gammas:
            for degree in degrees:
                classifier = svm.SVC(probability=True,kernel=kernel,C=c,gamma=gamma,degree=degree,max_iter=100000)
                params = {"kernel": kernel,"C": c,'gamma':gamma,'degree':degree}
                results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)

                model_index+=1
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [61]:
def train_test_CV_DecisionTree(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'DT'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    
    criterion = ["gini", "entropy"]
    splitter = ["best", "random"]
    min_samples_split = [2, 5, 10, 15,20]  # min number of data points placed in a node before the node is split, used to control over-fitting
    for c in criterion:
        for s in splitter:
            for min_split in min_samples_split:
                classifier = tree.DecisionTreeClassifier(criterion=c,splitter=s,min_samples_split=min_split)
                params = {"criterion": c,"splitter": s,'min_samples_split':min_split}
                results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)

                model_index+=1
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [62]:
def train_test_CV_NaiveBayes(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'NB'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    NB_Classifiers = [GaussianNB(), MultinomialNB()]
    # CategoricalNB()
    for NB_clf in NB_Classifiers:
        classifier = NB_clf  # create classifier
        params = {"NB_Classifiers": NB_clf}
        results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,
                                       metrics_results,results_summary,params)
        model_index+=1
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [63]:
def train_test_CV_KNN(folder_path_results,data,data_labels,metrics_results,best_models, ml_results):
    model_index = int(1)
    results_summary = pd.DataFrame(columns=['Algorithm','model_index', 'parameters',
                                               'FNR','FPR','MCC','ACC','F1score','F2score'])
    Algorithm = 'KNN'
#     Type = data_labels['Type']
#     data_labels = data_labels.drop("Type",axis=1)
    n_neighbors = range(1, 11)
    weights = ['uniform', 'distance']
    Algorithms = ['auto', 'ball_tree', 'kd_tree', 'brute']  # Algorithm used to compute the nearest neighbors
    for n in n_neighbors:
        for w in weights:
            for alg in Algorithms:
                classifier = KNeighborsClassifier(n_neighbors=n,weights=w,algorithm=alg)  # create classifier
                params = {"n_neighbors": n,'weights':w,"Algorithm":alg}
                results_summary = CV_model_tunning(data,data_labels,classifier,Algorithm,model_index,metrics_results,results_summary,params)

                model_index+=1
    print(Algorithm,'_results_summary was created')
    results_summary.to_csv(folder_path_results+'\\'+Algorithm+'_results_summary.csv')
    ml_results,best_models,best_model_index = print_and_summarize_best_model(results_summary,ml_results,best_models)
    return ml_results,best_models,metrics_results   

In [64]:
def conduct_tunning_and_classification_for_each_family_model_CV(data,data_labels,stage):
    best_models = init_best_models()
    ml_results = init_ml_results()
    metrics_results = init_metrics()
    folder_path = 'C:\\Users\\noy\\Desktop\\תזה\\Results\\Binary_Classification\\Kedma&Lavi'
    folder_path_results = folder_path+'\\classifiers'
    print('DecisionTree')
    ml_results,best_models,metrics_results = train_test_CV_DecisionTree(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('RandomForest')
    ml_results,best_models,metrics_results = train_test_CV_RandomForest(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('NaiveBayes')
    ml_results,best_models,metrics_results = train_test_CV_NaiveBayes(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('KNN')
    ml_results,best_models,metrics_results = train_test_CV_KNN(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('svm_linear')
    ml_results,best_models,metrics_results = train_test_CV_svm_linear(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('svm_rbf')
    ml_results,best_models,metrics_results = train_test_CV_svm_rbf(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('svm_poly')
    ml_results,best_models,metrics_results = train_test_CV_svm_poly(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    print('LogisticRegression')
    ml_results,best_models,metrics_results = train_test_CV_LogisticRegression(folder_path_results,data,data_labels,metrics_results,best_models, ml_results)
    
    best_models = pd.concat([best_models.drop(['FNR'], axis=1),best_models['FNR'].apply(pd.Series)], axis=1)
    ml_results = pd.concat([ml_results.drop(['FNR'], axis=1),ml_results['FNR'].apply(pd.Series)], axis=1)
   
    best_models = best_models.reindex(columns=['Algorithm',
                                               'model_index',
                                               'MCC',
                                               'ACC',
                                              'F1score',
                                              'F2score',
                                              'FNR',
                                              'FPR',
                                              'FNR_Leak',
                                              'FNR_Clog',
                                               'balanced_ACC']).reset_index().drop(['index'],axis=1)
    
    best_models.iloc[:,2:] = best_models.iloc[:,2:].round(5)
    best_models =best_models.set_index('Algorithm')
    best_models=best_models.T
    ml_results = ml_results.sort_values(by=[metric_to_optimize],ascending = False)  

    best_models.to_csv(folder_path+'\\best_models_include_malf_metrics.csv')
    ml_results.to_csv(folder_path+'\\ml_results_include_malf_metrics.csv')
    return ml_results,best_models,metrics_results

In [65]:
def RFECV_Random_Forest(X,y):
    from numpy import mean
    from numpy import std
    from sklearn.datasets import make_classification
    from sklearn.model_selection import cross_val_score
    from sklearn.model_selection import RepeatedStratifiedKFold
    from sklearn.feature_selection import RFECV
    from sklearn.ensemble import RandomForestClassifier
    from sklearn.pipeline import Pipeline
    from sklearn.metrics import matthews_corrcoef
    import sklearn.metrics as m
    from sklearn.metrics import fbeta_score, make_scorer
    
    ftwo_scorer = make_scorer(fbeta_score, beta=2)

    # Automatically select the number of features for RFE
    # create pipeline
    rfe = RFECV(estimator=RandomForestClassifier())

    model = RandomForestClassifier()
    pipeline = Pipeline(steps=[('s',rfe),('m',model)])
    # evaluate model
    cv = RepeatedStratifiedKFold(n_splits=5,n_repeats=5, random_state=12)
    
    n_scores = cross_val_score(pipeline, X, y, scoring=ftwo_scorer, cv=cv, n_jobs=-1, error_score='raise')
    # report performance
    print('Accuracy: %.3f (%.3f)' % (mean(n_scores), std(n_scores)))
    rfe.fit(X, y)
    
    plt.figure()
    plt.xlabel("Number of features selected")
    plt.ylabel("Cross validation score \n of number of selected features")
    plt.plot(range(1, len(rfe.grid_scores_)+1), rfe.grid_scores_)
    plt.show()

    print('The optimal number of features is {}'.format(rfe.n_features_))
    features = [f for f,s in zip(X.columns, rfe.support_) if s]
    print('The selected features are:')
    print ('{}'.format(features))
    
    for i in range(X.shape[1]):
        print('Column: %d, Selected %s, Rank: %.3f' % (i, rfe.support_[i], rfe.ranking_[i]))
    
    return features

### Define dataset

In [66]:
df = pd.read_excel(os.path.join(os.getcwd(), 'data_Kedma&Lavi_afer_DataPreparation.xlsx')).iloc[: , 1:] 
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 393 entries, 0 to 392
Data columns (total 27 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   RTK_Num_All_Plots_Data  393 non-null    int64  
 1   Plot_All_Plots_Data     393 non-null    object 
 2   Site_Name               393 non-null    object 
 3   min                     393 non-null    float64
 4   prctile5                393 non-null    float64
 5   prctile95               393 non-null    float64
 6   std                     393 non-null    float64
 7   MTD                     393 non-null    float64
 8   median                  393 non-null    float64
 9   skewness                393 non-null    float64
 10  IQR                     393 non-null    float64
 11  meanci_1                393 non-null    float64
 12  meanci_2                393 non-null    float64
 13  Diff_median_of_plot     393 non-null    float64
 14  Diff_std_of_plot        393 non-null    fl

In [67]:
df.loc[df.Type == 'Clog', 'Y_binary'] =1 #malfunction
df.loc[df.Type == 'Leak', 'Y_binary'] = 1 #malfunction
df.loc[df.Type == 'Control', 'Y_binary'] = 0 
y = df[["Type",'Y_binary']].copy(True)
X=df.drop(["Type",'Y_binary','Y'],axis=1).copy(True)
random.seed(10)

data_train, data_test, data_labels_train, data_labels_test = train_test_split(X, y, test_size=0.33, random_state=42)
# X_train.info()
vars_to_drop = ["RTK_Num_All_Plots_Data",'Plot_All_Plots_Data','Site_Name','SWP']

## Recursive featue elimination - cross validation based on RF

Selecting features using RFECV with RF and score F2score - as FN (miss malfunction is more important)

In [68]:
random.seed(10)
# features = RFECV_Random_Forest(data_train.drop(vars_to_drop,axis=1),data_labels_train['Y_binary'])


In [69]:
features = ['min', 'prctile5', 'prctile95', 'std', 'skewness', 'IQR', 'Diff_median_of_plot', 'Diff_std_of_plot', 'Diff_mean_of_row', 'Diff_std_of_row', 'prctile33', 'median_first_ring', 'median_second_ring', 'median_third_ring', 'median_core', 'CWSI_minus_CWSI_of_row']

In [70]:
ml_results,best_models,metrics_results = conduct_tunning_and_classification_for_each_family_model_CV(data_train[features],data_labels_train,stage='')

DecisionTree
DT _results_summary was created
RandomForest
RF _results_summary was created
NaiveBayes
NB _results_summary was created
KNN
KNN _results_summary was created
svm_linear


C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'


svm_linear _results_summary was created
svm_rbf
svm_rbf _results_summary was created
svm_poly


C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Cons

C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn('Solver terminated early (max_iter=%i).'
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\svm\_base.py:255: ConvergenceWarning: Solver terminated early (max_iter=100000).  Cons

...

C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linea

C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linea

C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linea

C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1317: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=none)
  warnings.warn("l1_ratio parameter is only used when penalty is "
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linear_model\_logistic.py:1322: UserWarning: Setting penalty='none' will ignore the C and l1_ratio parameters
  warnings.warn(
C:\Users\noy\Anaconda3\envs\seaversioneleven\lib\site-packages\sklearn\linea

LogisticRegression _results_summary was created


In [71]:
best_models#.sort_values(by=[metric_to_optimize],ascending=False )

Algorithm           DT        RF        NB       KNN svm_linear   svm_rbf  \
model_index         20       115         1        73          1        20   
MCC           0.202338  0.286292  0.173007  0.269619        0.0  0.308223   
ACC           0.626763  0.661451  0.621974  0.641001   0.631205  0.670668   
F1score       0.701757  0.724026  0.708321  0.693993   0.773887  0.731446   
F2score       0.702064  0.716733  0.723411  0.665207   0.895347  0.722016   
FNR            0.29668   0.28727   0.26553   0.35201        0.0   0.28321   
FPR           0.505158  0.427474  0.570947  0.371368        1.0  0.408105   
FNR_Leak       0.33037   0.32974   0.32589   0.41976        0.0   0.33643   
FNR_Clog       0.20015   0.15892   0.07483    0.1282        0.0   0.11632   
balanced_ACC   0.59908   0.64263   0.58176   0.63831        0.5   0.65434   

Algorithm     svm_poly LogisticRegression  
model_index         17                 14  
MCC           0.256139           0.108083  
ACC           0.648665           0.555951  
F1score       0.715082           0.611577  
F2score       0.708202           0.577095  
FNR             0.2954            0.44339  
FPR              0.448           0.445053  
FNR_Leak       0.31324            0.46238  
FNR_Clog       0.22402            0.37947  
balanced_ACC    0.6283            0.55578

### Saving folds results for T-test

In [36]:
params = {'n_estimators': 500, 'criterion': 'entropy', 'min_samples_split': 10, 'bootstrap': True, 'max_depth': 8}
Algorithm = 'RF_115_binary'
    
classifier = RandomForestClassifier(random_state=12,class_weight='balanced',
                                    n_estimators=500,max_depth=8, criterion='entropy',
                                    min_samples_split=10,bootstrap=True)  # class_weight: misclassifying the rare class is punished harsher.
Type = data_labels_train['Type']
data_labels = data_labels_train.drop("Type",axis=1)
data =data_train[features]
data_labels
FNR_results, Fold_num, MCC_results, ACC_results,F1score_results,F2score_results = [],[],[],[],[],[]                      
random.seed(10)
skf = RepeatedStratifiedKFold(n_splits=5,n_repeats=5, random_state=12)
fold=1
# K_folds:
for train_index, test_index in skf.split(data, data_labels):
    x_train_fold, x_test_fold = data.iloc[train_index], data.iloc[test_index]
    y_train_fold, y_test_fold = data_labels.iloc[train_index], data_labels.iloc[test_index]
    Type_test = Type.iloc[test_index]

    if (Algorithm not in ('RF','DT')):
        if (Algorithm in('NB','svm_linear')):
            scaler = MinMaxScaler()
        else:
            scaler = StandardScaler()
        x_train_fold = scaler.fit_transform(x_train_fold)
        x_test_fold = scaler.fit_transform(x_test_fold)

    classifier.fit(x_train_fold, y_train_fold.values.ravel())
    y_prediction = classifier.predict(x_test_fold)
    metrics_results = calculate_metrics(Algorithm,y_test_fold,y_prediction,metrics_results,Type_test)
    Fold_num.append(fold)
    MCC_results.append(metrics_results['MCC'][Algorithm])
    FNR_results.append(metrics_results['FNR'][Algorithm])
    F1score_results.append(metrics_results['F1score'][Algorithm])
    F2score_results.append(metrics_results['F2score'][Algorithm])
    fold =fold+1
balanced_ACC_results = pd.DataFrame(d['balanced_ACC'] for d in FNR_results).values.ravel()
balanced_ACC_results

results_summary= pd.DataFrame(data={'Algorithm':Algorithm,
                                              'Fold_number':Fold_num,
                                              'MCC': MCC_results,
                                               'balanced_ACC':balanced_ACC_results,
                                              'F1score': F1score_results,
                                              'F2score': F2score_results})
results_summary =results_summary.set_index('Fold_number')
results_summary
Algorithm = 'RF_115_binary'
folder_path = 'C:\\Users\\noy\\Desktop\\תזה\\Results\\Kedma_and_Lavi_secend_best_model_'
results_summary.to_csv(folder_path+Algorithm+'_folds_results.csv')

## Evaluating model on independent data set

In [66]:
#train
data_train = data
data_labels_train = data_labels
data_labels_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 278 entries, 184 to 102
Data columns (total 1 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Y_binary  278 non-null    float64
dtypes: float64(1)
memory usage: 4.3 KB


In [62]:
#test
data_test = X_test[features].copy()
data_labels_test = y_test.drop("Type",axis=1)
data_labels_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 137 entries, 55 to 172
Data columns (total 1 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Y_binary  137 non-null    float64
dtypes: float64(1)
memory usage: 2.1 KB


In [73]:
results = init_metrics()
Algorithm = 'svm_rbf'
{'kernel': 'rbf', 'C': 10, 'gamma': 0.1}


classifier = RandomForestClassifier(random_state=12,class_weight='balanced', 
                                    n_estimators=params['n_estimators'],
                                    max_depth=params['max_depth'], criterion=params['criterion'],
                                    min_samples_split=params['min_samples_split'],
                                    bootstrap=params['bootstrap'])  # class_weight: misclassifying the rare class is punished harsher.

classifier.fit(data_train, data_labels_train.values.ravel())
y_prediction = classifier.predict(data_test)
results = calculate_metrics(Algorithm,data_labels_test,y_prediction,results)
results_summary = pd.DataFrame([[Algorithm,*list(params.values()),
                                      results['FNR'][Algorithm], results['FPR'][Algorithm],
                                     results['MCC'][Algorithm], results['ACC'][Algorithm],
                                     results['F1score'][Algorithm], results['F2score'][Algorithm]]],
            columns=['Algorithm',*list(params.keys()),'FNR','FPR', 'MCC', 'ACC','F1score','F2score'])

results_summary

Algorithm       FNR       FPR       MCC       ACC   F1score   F2score
0  Random Forest  0.266667  0.468085  0.262714  0.664234  0.741573  0.736607